Instalando Pacote

In [1]:
!git clone https://github.com/huggingface/transformers;
!cd transformers; pip3 install .

Cloning into 'transformers'...
remote: Enumerating objects: 159654, done.
remote: Counting objects: 100% (1106/1106), done.
remote: Compressing objects: 100% (661/661), done.
remote: Total 159654 (delta 582), reused 634 (delta 359), pack-reused 158548
Receiving objects: 100% (159654/159654), 161.18 MiB | 25.18 MiB/s, done.
Resolving deltas: 100% (119616/119616), done.
Processing /content/transformers
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.9/294.9 kB 5.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 54.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 74.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 24.9 MB/s eta 0:00:00
  Created wheel for transformers: filename=transformers-4.34.0.dev0-py3-none-any.whl size=7700260 sha256=dca09dc112bd6b6bf67108e43a76a526e4e8

In [2]:
! pip install simpletransformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 250.8/250.8 kB 3.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 519.6/519.6 kB 10.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 4.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 15.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.1/8.1 MB 29.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 36.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 189.5/189.5 kB 17.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.8/224.8 kB 21.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 10.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 7.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 12.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [3]:
! pip install datasets

Puxando Dataset de Discurso de Ódio

In [4]:
from google.colab import drive
drive.mount('drive')

Mounted at drive


In [5]:
import pandas as pd
import transformers
from transformers import AutoModel, BertTokenizerFast
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
from transformers import AdamW
import tensorflow as tf
import numpy as np
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from sklearn.metrics import accuracy_score, f1_score
from sklearn.utils.class_weight import compute_class_weight
from sklearn.linear_model import SGDClassifier
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import CountVectorizer



# link: https://huggingface.co/datasets/ag_news

In [6]:
test = pd.read_csv('/content/drive/My Drive/Colab Notebooks/t5_key_text/original/base_tweet_sentiment_test.csv', sep = ';', decimal = ',')
test.head()

text  label
0  @user @user what do these '1/2 naked pics' hav...      1
1  OH: “I had a blue penis while I was this” [pla...      1
2  @user @user That's coming, but I think the vic...      1
3  I think I may be finally in with the in crowd ...      2
4  @user Wow,first Hugo Chavez and now Fidel Cast...      0

In [7]:
# X_train = dataset['train']['text']
X_test = test['text']
# y_train = dataset['train']['label']
y_test = test['label']

In [8]:
nclasses = len(np.unique(y_test))

In [9]:
nclasses

3

In [10]:
def puxa_dados_normal(caminho):
  csv = pd.read_csv(caminho, sep = ';', decimal = ',')
  original = csv[['texto', 'label']].copy()
  original = original.drop_duplicates()

  # csv = csv[csv['similiaridade_parafrase'] >= 0.95].copy()


  parafrase = csv[['generated', 'label']].copy()
  parafrase = parafrase.drop_duplicates()
  parafrase = parafrase[~(parafrase['generated'].isnull())].copy()
  parafrase.rename(columns={"generated": "texto"}, inplace = True)

  fim = original.append(parafrase)

  fim = fim.sample(frac=1)

  X = fim['texto'].values
  y = fim['label'].values


  return X, y


In [11]:
def puxa_original(caminho):
  csv = pd.read_csv(caminho, sep = ';', decimal = ',')

  X = csv['texto'].values
  y = csv['label'].values


  return X, y

In [12]:
def puxa_dados_normal_pkl(caminho):
  csv = pd.read_pickle(caminho)
  original = csv[['texto', 'label']].copy()
  original = original.drop_duplicates()

  # csv = csv[csv['similiaridade_parafrase'] >= 0.95].copy()


  parafrase = csv[['generated', 'label']].copy()
  # parafrase = parafrase.drop_duplicates()
  parafrase = parafrase[~(parafrase['generated'].isnull())].copy()
  parafrase.rename(columns={"generated": "texto"}, inplace = True)

  fim = original.append(parafrase)

  fim = fim.sample(frac=1)

  X = fim['texto'].values
  y = fim['label'].values


  return X, y


In [14]:
def puxa_dados_lambada(caminho, original):
  csv = pd.read_csv(caminho, sep = ';', decimal = ',')
  original = pd.read_csv(original, sep = ';', decimal = ',')

  # csv = csv[csv['similiaridade_parafrase'] >= 0.95].copy()


  parafrase = csv[['generated', 'new_label']].copy()
  # parafrase = parafrase.drop_duplicates()
  parafrase = parafrase[~(parafrase['generated'].isnull())].copy()
  parafrase.rename(columns={"generated": "texto", "new_label": "label"}, inplace = True)

  fim = original.append(parafrase)

  fim = fim.sample(frac=1)

  X = fim['texto'].values
  y = fim['label'].values


  return X, y

In [15]:
def puxa_dados_lambada_filtro(caminho, original, limiar):
  csv = pd.read_csv(caminho, sep = ';', decimal = ',')
  original = pd.read_csv(original, sep = ';', decimal = ',')

  csv = csv[csv['prob_text'] >= limiar].copy()


  parafrase = csv[['generated', 'new_label']].copy()
  parafrase = parafrase.drop_duplicates()
  parafrase = parafrase[~(parafrase['generated'].isnull())].copy()
  parafrase.rename(columns={"generated": "texto", "new_label": "label"}, inplace = True)

  fim = original.append(parafrase)

  fim = fim.sample(frac=1)

  X = fim['texto'].values
  y = fim['label'].values


  return X, y

In [16]:
def puxa_dados_lambada_pkl_filtro(caminho, original, limiar):
  csv = pd.read_pickle(caminho)
  original = pd.read_csv(original, sep = ';', decimal = ',')

  csv = csv[csv['prob_text'] >= limiar].copy()


  parafrase = csv[['generated', 'new_label']].copy()
  parafrase = parafrase.drop_duplicates()
  parafrase = parafrase[~(parafrase['generated'].isnull())].copy()
  parafrase.rename(columns={"generated": "texto", "new_label": "label"}, inplace = True)

  fim = original.append(parafrase)

  fim = fim.sample(frac=1)

  X = fim['texto'].values
  y = fim['label'].values


  return X, y

In [17]:
def desempenho_LSTM(X_train, X_test, y_train, y_test, classes, num_epochs ):


  # vocab_size = 10000
  embedding_dim = 300
  max_length = 128
  trunc_type = 'post'
  padding_type = 'post'
  oov_tok = '<OOV>'

  tokenizer = Tokenizer( oov_token=oov_tok)
  tokenizer.fit_on_texts(X_train)
  word_index = tokenizer.word_index
  vocab_size = len(word_index)+1

  train_sequences = tokenizer.texts_to_sequences(X_train)
  # val_sequences = tokenizer.texts_to_sequences(X_val)

  train_padded = pad_sequences(train_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)
  # val_padded = pad_sequences(val_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)

  # model = tf.keras.Sequential([
  #   # Camada Embedding (reduzir dimensionalidade)
  #   tf.keras.layers.Embedding(vocab_size, embedding_dim),
  #   # Camada de LSTM bidirecional
  #   tf.keras.layers.LSTM(embedding_dim),
  #   # Camada densa com Relu
  #   tf.keras.layers.Dense(embedding_dim, activation='relu'),
  #   #Camada de saída para as 4 classes
  #   tf.keras.layers.Dense(classes, activation='softmax')
  #   ])
  model = tf.keras.models.Sequential([
        tf.keras.layers.Embedding(input_dim=vocab_size,
                                  mask_zero= True,
                                  output_dim=embedding_dim,
                                  input_length=max_length,
                                  input_shape=(max_length, )),

        tf.keras.layers.Bidirectional(tf.keras.layers.LSTM(32, return_sequences=True)),
        tf.keras.layers.Bidirectional(tf.keras.layers.LSTM(32, return_sequences=False)),
        tf.keras.layers.Dense(64, activation='relu'),
        tf.keras.layers.Dropout(0.5),
        tf.keras.layers.Dense(units=classes, activation='softmax')
    ])
  # model = tf.keras.Sequential()
  # model.add(tf.keras.layers.Embedding(vocab_size, embedding_dim))
  # model.add(tf.keras.layers.Conv1D(filters=32, kernel_size=3, padding='same', activation='relu'))
  # model.add(tf.keras.layers.MaxPooling1D(pool_size=2))
  # model.add(tf.keras.layers.LSTM(100))
  # model.add(tf.keras.layers.Dense(classes, activation='softmax'))

  model.compile(loss='sparse_categorical_crossentropy', optimizer='adam', metrics=['accuracy'])


  history = model.fit(train_padded, y_train, epochs=num_epochs, verbose=2)

  test_sequences = tokenizer.texts_to_sequences(X_test)
  test_padded = pad_sequences(test_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)


  preds_log = model.predict(test_padded)
  preds = tf.argmax(preds_log, 1)
  acc = accuracy_score(y_test, preds)
  f1 = f1_score(y_test, preds, average='macro')

  return acc, f1







In [18]:
def desempenho_CNN(X_train, X_test, y_train, y_test, classes, num_epochs ):


  # vocab_size = 10000
  embedding_dim = 300
  max_length = 128
  trunc_type = 'post'
  padding_type = 'post'
  oov_tok = '<OOV>'

  tokenizer = Tokenizer( oov_token=oov_tok)
  tokenizer.fit_on_texts(X_train)
  word_index = tokenizer.word_index
  vocab_size = len(word_index)+1

  train_sequences = tokenizer.texts_to_sequences(X_train)
  # val_sequences = tokenizer.texts_to_sequences(X_val)

  train_padded = pad_sequences(train_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)
  # val_padded = pad_sequences(val_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)

  # model = tf.keras.Sequential([
  #   # Camada Embedding (reduzir dimensionalidade)
  #   tf.keras.layers.Embedding(vocab_size, embedding_dim),
  #   # Camada de LSTM bidirecional
  #   tf.keras.layers.LSTM(embedding_dim),
  #   # Camada densa com Relu
  #   tf.keras.layers.Dense(embedding_dim, activation='relu'),
  #   #Camada de saída para as 4 classes
  #   tf.keras.layers.Dense(classes, activation='softmax')
  #   ])
  model = tf.keras.models.Sequential([
        tf.keras.layers.Embedding(input_dim=vocab_size,
                                  mask_zero= True,
                                  output_dim=embedding_dim,
                                  input_length=max_length,
                                  input_shape=(max_length, )),

        tf.keras.layers.Conv1D(filters=100, kernel_size = 3, activation = 'relu',
                               # set 'axis' value to the first and second axis of conv1D weights (rows, cols)
                               kernel_constraint= MaxNorm( max_value=3, axis=[0,1])),

        tf.keras.layers.MaxPool1D(2),
        tf.keras.layers.Flatten(),
        tf.keras.layers.Dropout(0.5),
        tf.keras.layers.Dense(10, activation='relu',
                              # set axis to 0 to constrain each weight vector of length (input_dim,) in dense layer
                              kernel_constraint = MaxNorm( max_value=3, axis=0)),
        tf.keras.layers.Dropout(0.5),
        tf.keras.layers.Dense(units=classes, activation='softmax')
    ])
  # model = tf.keras.Sequential()
  # model.add(tf.keras.layers.Embedding(vocab_size, embedding_dim))
  # model.add(tf.keras.layers.Conv1D(filters=32, kernel_size=3, padding='same', activation='relu'))
  # model.add(tf.keras.layers.MaxPooling1D(pool_size=2))
  # model.add(tf.keras.layers.LSTM(100))
  # model.add(tf.keras.layers.Dense(classes, activation='softmax'))

  model.compile(loss='sparse_categorical_crossentropy', optimizer='adam', metrics=['accuracy'])


  history = model.fit(train_padded, y_train, epochs=num_epochs, verbose=2)

  test_sequences = tokenizer.texts_to_sequences(X_test)
  test_padded = pad_sequences(test_sequences, maxlen=max_length, padding=padding_type, truncating=trunc_type)


  preds_log = model.predict(test_padded)
  preds = tf.argmax(preds_log, 1)
  acc = accuracy_score(y_test, preds)
  f1 = f1_score(y_test, preds, average='macro')

  return acc, f1







In [19]:
# Evaluate the model
from sklearn.metrics import f1_score, accuracy_score

def f1_multiclass(labels, preds):
      return f1_score(labels, preds, average='macro')


In [20]:
def desempenho_transformers(X_train, X_test, y_train, y_test,classes, model,type_model, epochs, batch, max_len):
  from simpletransformers.classification import ClassificationModel
  import pandas as pd
  import logging
  import sklearn

  train_df = pd.DataFrame(X_train)
  train_df['target'] = y_train

  eval_df = pd.DataFrame(X_test)
  eval_df['target'] = y_test



  # Create a ClassificationModel
  model = ClassificationModel(type_model, model, num_labels=classes, args={'num_train_epochs':epochs,
                                                                           'train_batch_size':batch,
                                                                           'max_seq_length':max_len,
                                                                          #  "fp16":False,
                                                                           'overwrite_output_dir': True})

  # Train the model
  model.train_model(train_df)
  result, model_outputs, wrong_predictions = model.eval_model(eval_df, acc=sklearn.metrics.accuracy_score,f1=f1_multiclass)

  return result['acc'], result['f1']





In [21]:

y_test = np.array(y_test)


# Original

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_original(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/210 [00:00<?, ?it/s]

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Running Epoch 0 of 4:   0%|          | 0/7 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/7 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/12284 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/1536 [00:00<?, ?it/s]

Roberta
ACC:0.48380006512536633
F1:0.21897340587363381


In [ ]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.449935  0.339667   0.511397  0.345078     0.512537    0.365616
1  original2  0.443178  0.318664   0.467519  0.258469     0.506513    0.370592
2  original3  0.442364  0.326326   0.483312  0.241823     0.482660    0.377349
3  original4  0.404836  0.307204   0.512048  0.369240     0.491697    0.283382
4  original5  0.415174  0.320905   0.469391  0.334866     0.483800    0.218973

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.431097  0.322553   0.488733  0.309895     0.495441    0.323183
std    0.019818  0.011838   0.021856  0.056262     0.013488    0.069688
min    0.404836  0.307204   0.467519  0.241823     0.482660    0.218973
25%    0.415174  0.318664   0.469391  0.258469     0.483800    0.283382
50%    0.442364  0.320905   0.483312  0.334866     0.491697    0.365616
75%    0.443178  0.326326   0.511397  0.345078     0.506513    0.370592
max    0.449935  0.339667   0.512048  0.369240     0.512537    0.377349

# EDA

In [22]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/eda/base_tweet_sentiment_'+str(perc)+'_eda'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/eda/base_tweet_sentiment_'+str(perc)+'_eda'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/eda/base_tweet_sentiment_'+str(perc)+'_eda'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/eda/base_tweet_sentiment_'+str(perc)+'_eda'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/eda/base_tweet_sentiment_'+str(perc)+'_eda'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 1, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  1, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  1, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-10-a91fedf45f9b>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Loading the tokenizer from the `special_tokens_map.json` and the `added_tokens.json` will be removed in `transformers 5`,  it is kept for forward compatibility, but it is recommended to update your `tokenizer_config.json` by uploading it again. You will see the new `added_tokens_decoder` attribute that will store the relevant information.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/1890 [00:00<?, ?it/s]

...

Running Epoch 0 of 1:   0%|          | 0/60 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/12284 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/1536 [00:00<?, ?it/s]

Roberta
ACC:0.547704330836861
F1:0.4416445749140356


In [23]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [24]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.416802  0.313664   0.488033  0.238734     0.560729    0.511857
1  original2  0.501547  0.363215   0.522224  0.468684     0.525725    0.388852
2  original3  0.441631  0.328446   0.551205  0.527794     0.469065    0.368440
3  original4  0.483067  0.401783   0.617226  0.598425     0.653370    0.634746
4  original5  0.471833  0.355712   0.585640  0.546178     0.547704    0.441645

In [25]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.462976  0.352564   0.552866  0.475963     0.551319    0.469108
std    0.033754  0.034061   0.050895  0.140485     0.066964    0.107927
min    0.416802  0.313664   0.488033  0.238734     0.469065    0.368440
25%    0.441631  0.328446   0.522224  0.468684     0.525725    0.388852
50%    0.471833  0.355712   0.551205  0.527794     0.547704    0.441645
75%    0.483067  0.363215   0.585640  0.546178     0.560729    0.511857
max    0.501547  0.401783   0.617226  0.598425     0.653370    0.634746

# SSMBA

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/ssmba/base_tweet_sentiment_'+str(perc)+'_ssmba'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/ssmba/base_tweet_sentiment_'+str(perc)+'_ssmba'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/ssmba/base_tweet_sentiment_'+str(perc)+'_ssmba'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/ssmba/base_tweet_sentiment_'+str(perc)+'_ssmba'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/ssmba/base_tweet_sentiment_'+str(perc)+'_ssmba'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 1, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  1, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  1, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-10-a91fedf45f9b>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/1260 [00:00<?, ?it/s]

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/40 [00:00<?, ?it/s]

...

Running Epoch 0 of 1:   0%|          | 0/40 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/12284 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/1536 [00:00<?, ?it/s]

Roberta
ACC:0.5260501465320743
F1:0.39619673593020677


In [ ]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.487463  0.353850   0.492511  0.374939     0.527190    0.408426
1  original2  0.453273  0.329896   0.366493  0.277715     0.501791    0.295060
2  original3  0.413953  0.320199   0.450586  0.350014     0.504070    0.380063
3  original4  0.511071  0.354343   0.588815  0.549032     0.521817    0.387236
4  original5  0.398893  0.327892   0.499756  0.390973     0.526050    0.396197

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.452931  0.337236   0.479632  0.388534     0.516184    0.373396
std    0.047467  0.015813   0.080833  0.099643     0.012289    0.045054
min    0.398893  0.320199   0.366493  0.277715     0.501791    0.295060
25%    0.413953  0.327892   0.450586  0.350014     0.504070    0.380063
50%    0.453273  0.329896   0.492511  0.374939     0.521817    0.387236
75%    0.487463  0.353850   0.499756  0.390973     0.526050    0.396197
max    0.511071  0.354343   0.588815  0.549032     0.527190    0.408426

# Checklist

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/checklist/base_tweet_sentiment_'+str(perc)+'_checklist'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/checklist/base_tweet_sentiment_'+str(perc)+'_checklist'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/checklist/base_tweet_sentiment_'+str(perc)+'_checklist'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/checklist/base_tweet_sentiment_'+str(perc)+'_checklist'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/checklist/base_tweet_sentiment_'+str(perc)+'_checklist'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-10-a91fedf45f9b>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/978 [00:00<?, ?it/s]

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Running Epoch 0 of 4:   0%|          | 0/31 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/29 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/12284 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/1536 [00:00<?, ?it/s]

Roberta
ACC:0.6092478020188864
F1:0.606002363751208


In [ ]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.518805  0.438426   0.591583  0.571510     0.594350    0.565446
1  original2  0.578639  0.560365   0.596467  0.573295     0.643032    0.640708
2  original3  0.567079  0.518943   0.608759  0.593128     0.603387    0.603741
3  original4  0.540541  0.473233   0.611283  0.583713     0.612911    0.572602
4  original5  0.512862  0.410927   0.580918  0.581654     0.609248    0.606002

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.543585  0.480379   0.597802  0.580660     0.612585    0.597700
std    0.028931  0.060249   0.012523  0.008714     0.018408    0.030105
min    0.512862  0.410927   0.580918  0.571510     0.594350    0.565446
25%    0.518805  0.438426   0.591583  0.573295     0.603387    0.572602
50%    0.540541  0.473233   0.596467  0.581654     0.609248    0.603741
75%    0.567079  0.518943   0.608759  0.583713     0.612911    0.606002
max    0.578639  0.560365   0.611283  0.593128     0.643032    0.640708

# Back Translation

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/back_translation/base_tweet_sentiment_'+str(perc)+'_back_translation'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/back_translation/base_tweet_sentiment_'+str(perc)+'_back_translation'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/back_translation/base_tweet_sentiment_'+str(perc)+'_back_translation'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/back_translation/base_tweet_sentiment_'+str(perc)+'_back_translation'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/back_translation/base_tweet_sentiment_'+str(perc)+'_back_translation'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-10-a91fedf45f9b>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/420 [00:00<?, ?it/s]

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Running Epoch 0 of 4:   0%|          | 0/14 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/14 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/12284 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/1536 [00:00<?, ?it/s]

Roberta
ACC:0.5963855421686747
F1:0.5599763788679555


In [ ]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.525155  0.400361   0.502361  0.406911     0.531342    0.418487
1  original2  0.496418  0.376452   0.537040  0.441729     0.529469    0.394700
2  original3  0.433654  0.363665   0.411185  0.251419     0.465402    0.357321
3  original4  0.508629  0.364562   0.581325  0.547090     0.554135    0.429963
4  original5  0.501791  0.378604   0.533621  0.463939     0.596386    0.559976

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.493129  0.376729   0.513106  0.422218     0.535347    0.432089
std    0.034961  0.014839   0.063543  0.108537     0.047491    0.076702
min    0.433654  0.363665   0.411185  0.251419     0.465402    0.357321
25%    0.496418  0.364562   0.502361  0.406911     0.529469    0.394700
50%    0.501791  0.376452   0.533621  0.441729     0.531342    0.418487
75%    0.508629  0.378604   0.537040  0.463939     0.554135    0.429963
max    0.525155  0.400361   0.581325  0.547090     0.596386    0.559976

#LAMBADA

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/lambada/base_tweet_sentiment_'+str(perc)+'_lambada'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/lambada/base_tweet_sentiment_'+str(perc)+'_lambada'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/lambada/base_tweet_sentiment_'+str(perc)+'_lambada'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/lambada/base_tweet_sentiment_'+str(perc)+'_lambada'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/lambada/base_tweet_sentiment_'+str(perc)+'_lambada'+str(i+5)+'.csv',
       ]
borig = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_lambada(arqs[j], borig[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 1, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  1, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  1, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-12-df95bd675bd6>:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/1260 [00:00<?, ?it/s]

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/40 [00:00<?, ?it/s]

...

Running Epoch 0 of 1:   0%|          | 0/40 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/12284 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/1536 [00:00<?, ?it/s]

Roberta
ACC:0.4833116248778899
F1:0.217221886833873


In [ ]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.483312  0.217222   0.483312  0.217222     0.483312    0.217222
1  original2  0.483312  0.217222   0.483312  0.217222     0.483312    0.217222
2  original3  0.483312  0.217222   0.483312  0.217222     0.483312    0.217222
3  original4  0.483312  0.217222   0.483312  0.217222     0.483312    0.217222
4  original5  0.483312  0.217222   0.483312  0.217222     0.483312    0.217222

In [ ]:
base_resultados.describe()

BERT_ACC       BERT_F1  XLNET_ACC      XLNET_F1  ROBERTA_ACC  \
count  5.000000  5.000000e+00   5.000000  5.000000e+00     5.000000   
mean   0.483312  2.172219e-01   0.483312  2.172219e-01     0.483312   
std    0.000000  3.103168e-17   0.000000  3.103168e-17     0.000000   
min    0.483312  2.172219e-01   0.483312  2.172219e-01     0.483312   
25%    0.483312  2.172219e-01   0.483312  2.172219e-01     0.483312   
50%    0.483312  2.172219e-01   0.483312  2.172219e-01     0.483312   
75%    0.483312  2.172219e-01   0.483312  2.172219e-01     0.483312   
max    0.483312  2.172219e-01   0.483312  2.172219e-01     0.483312   

         ROBERTA_F1  
count  5.000000e+00  
mean   2.172219e-01  
std    3.103168e-17  
min    2.172219e-01  
25%    2.172219e-01  
50%    2.172219e-01  
75%    2.172219e-01  
max    2.172219e-01

# Contrastive LAMBADA

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/lambada/base_tweet_sentiment_'+str(perc)+'_lambada_contrastive'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/lambada/base_tweet_sentiment_'+str(perc)+'_lambada_contrastive'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/lambada/base_tweet_sentiment_'+str(perc)+'_lambada_contrastive'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/lambada/base_tweet_sentiment_'+str(perc)+'_lambada_contrastive'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/lambada/base_tweet_sentiment_'+str(perc)+'_lambada_contrastive'+str(i+5)+'.csv',
       ]
borig = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_lambada(arqs[j], borig[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 1, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  1, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  1, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-12-df95bd675bd6>:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/1260 [00:00<?, ?it/s]

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/40 [00:00<?, ?it/s]

...

Running Epoch 0 of 1:   0%|          | 0/40 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/12284 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/1536 [00:00<?, ?it/s]

Roberta
ACC:0.32692933897753174
F1:0.26017408960083016


In [ ]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.387984  0.360414   0.494057  0.314934     0.445376    0.362953
1  original2  0.514246  0.361620   0.491289  0.261782     0.483312    0.217222
2  original3  0.489906  0.250579   0.411104  0.310648     0.483312    0.217222
3  original4  0.312683  0.253738   0.331732  0.267403     0.421768    0.326493
4  original5  0.424455  0.319524   0.464832  0.314041     0.326929    0.260174

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.425855  0.309175   0.438603  0.293762     0.432139    0.276813
std    0.080869  0.054749   0.068404  0.026750     0.064399    0.065703
min    0.312683  0.250579   0.331732  0.261782     0.326929    0.217222
25%    0.387984  0.253738   0.411104  0.267403     0.421768    0.217222
50%    0.424455  0.319524   0.464832  0.310648     0.445376    0.260174
75%    0.489906  0.360414   0.491289  0.314041     0.483312    0.326493
max    0.514246  0.361620   0.494057  0.314934     0.483312    0.362953

# LLAMA 2 Paraphraser

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/gptparaphrase/base_tweet_sentiment_'+str(perc)+'_gptparaphrase'+str(i+1)+'.pkl',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/gptparaphrase/base_tweet_sentiment_'+str(perc)+'_gptparaphrase'+str(i+2)+'.pkl',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/gptparaphrase/base_tweet_sentiment_'+str(perc)+'_gptparaphrase'+str(i+3)+'.pkl',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/gptparaphrase/base_tweet_sentiment_'+str(perc)+'_gptparaphrase'+str(i+4)+'.pkl',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/gptparaphrase/base_tweet_sentiment_'+str(perc)+'_gptparaphrase'+str(i+5)+'.pkl',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal_pkl(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet', 4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-53-8a66c1fcd9f8>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/1231 [00:00<?, ?it/s]

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Running Epoch 0 of 4:   0%|          | 0/39 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/39 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/12284 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/1536 [00:00<?, ?it/s]

Roberta
ACC:0.5839303158580267
F1:0.5676372123949928


In [ ]:
data = {'Aug': [ 'original1', 'original2', 'original3', 'original4','original5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  original1  0.525643  0.483968   0.571638  0.546245     0.577255    0.538589
1  original2  0.568870  0.536934   0.583279  0.568188     0.621540    0.605204
2  original3  0.491452  0.403386   0.586942  0.582811     0.629681    0.628809
3  original4  0.574813  0.535076   0.579372  0.541529     0.612341    0.596116
4  original5  0.550309  0.509635   0.596874  0.583555     0.583930    0.567637

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.542218  0.493800   0.583621  0.564466     0.604950    0.587271
std    0.034242  0.054969   0.009333  0.019830     0.023186    0.034931
min    0.491452  0.403386   0.571638  0.541529     0.577255    0.538589
25%    0.525643  0.483968   0.579372  0.546245     0.583930    0.567637
50%    0.550309  0.509635   0.583279  0.568188     0.612341    0.596116
75%    0.568870  0.535076   0.586942  0.582811     0.621540    0.605204
max    0.574813  0.536934   0.596874  0.583555     0.629681    0.628809

# ProtAugment

In [26]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/protaugment/base_tweet_sentiment_'+str(perc)+'_protaugment'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/protaugment/base_tweet_sentiment_'+str(perc)+'_protaugment'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/protaugment/base_tweet_sentiment_'+str(perc)+'_protaugment'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/protaugment/base_tweet_sentiment_'+str(perc)+'_protaugment'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/protaugment/base_tweet_sentiment_'+str(perc)+'_protaugment'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_normal(arqs[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet', 4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-10-a91fedf45f9b>:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/1201 [00:00<?, ?it/s]

Epoch:   0%|          | 0/4 [00:00<?, ?it/s]

Running Epoch 0 of 4:   0%|          | 0/38 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/38 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/12284 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/1536 [00:00<?, ?it/s]

Roberta
ACC:0.617551286225985
F1:0.596588436246855


In [27]:
data = {'Aug': [ 'eda1', 'eda2', 'eda3', 'eda4','eda5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [28]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.558417  0.517282   0.607587  0.594404     0.618170    0.597426
std    0.027491  0.020453   0.017915  0.015890     0.007178    0.006107
min    0.518317  0.483955   0.580593  0.570337     0.611934    0.589716
25%    0.557066  0.518005   0.602572  0.591095     0.614376    0.593782
50%    0.558043  0.519155   0.607050  0.595349     0.616574    0.596588
75%    0.562927  0.526078   0.623820  0.601723     0.617551    0.602661
max    0.595734  0.539217   0.623901  0.613518     0.630414    0.604380

# GPTNEOKEY

In [ ]:
perc = 5
i=0
from tensorflow.keras import regularizers
from tensorflow.keras.constraints import MaxNorm
arqs = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/teste_algo/base_tweet_sentiment_'+str(perc)+'_gptneokey'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/teste_algo/base_tweet_sentiment_'+str(perc)+'_gptneokey'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/teste_algo/base_tweet_sentiment_'+str(perc)+'_gptneokey'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/teste_algo/base_tweet_sentiment_'+str(perc)+'_gptneokey'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/teste_algo/base_tweet_sentiment_'+str(perc)+'_gptneokey'+str(i+5)+'.csv',
       ]
borig = [
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+1)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+2)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+3)+'.csv',
        '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+4)+'.csv',
       '/content/drive/My Drive/Colab Notebooks/t5_key_text/perc_' +str(perc) + '/tweet_sentiment/base_tweet_sentiment_'+str(perc)+'_original'+str(i+5)+'.csv',
       ]

cnn_acc = []
cnn_f1 = []
lstm_acc = []
lstm_f1 = []
bert_acc = []
bert_f1 = []
xlnet_acc = []
xlnet_f1 = []
roberta_acc = []
roberta_f1 = []
import gc
import pandas as pd
from sklearn.pipeline import Pipeline
from sklearn.svm import SVC
torch.cuda.empty_cache()
gc.collect()
for j in range(len(arqs)):
  print(j)
  X_train,  y_train = puxa_dados_lambada(arqs[j], borig[j])
  # svm = desempenho_CNN(X_train,  X_test, y_train,  y_test, nclasses, 15)
  # print('CNN')
  # print('ACC:' + str(svm[0]))
  # print('F1:' + str(svm[1]))
  # lstm = desempenho_LSTM(X_train,  X_test, y_train,  y_test, nclasses, 5)
  # print('LSTM')
  # print('ACC:' + str(lstm[0]))
  # print('F1:' + str(lstm[1]))
  # torch.cuda.empty_cache()
  # gc.collect()
  bert = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'bert-base-uncased','bert', 4, 32, 64)

  print('BERT')
  print('ACC:' + str(bert[0]))
  print('F1:' + str(bert[1]))

  torch.cuda.empty_cache()
  gc.collect()

  xlnet = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'xlnet-base-cased','xlnet',  4, 32, 64)
  print('XlNet')
  print('ACC:' + str(xlnet[0]))
  print('F1:' + str(xlnet[1]))

  torch.cuda.empty_cache()
  gc.collect()

  roberta = desempenho_transformers(X_train, X_test, y_train, y_test, nclasses, 'roberta-base','roberta',  4, 32, 64)
  print('Roberta')
  print('ACC:' + str(roberta[0]))
  print('F1:' + str(roberta[1]))

  # cnn_acc.append(svm[0])
  # cnn_f1.append(svm[1])

  # lstm_acc.append(lstm[0])
  # lstm_f1.append(lstm[1])

  bert_acc.append(bert[0])
  bert_f1.append(bert[1])

  xlnet_acc.append(xlnet[0])
  xlnet_f1.append(xlnet[1])

  roberta_acc.append(roberta[0])
  roberta_f1.append(roberta[1])

0


<ipython-input-12-df95bd675bd6>:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  fim = original.append(parafrase)


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:612: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/1260 [00:00<?, ?it/s]

...

Running Epoch 3 of 4:   0%|          | 0/40 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/classification/classification_model.py:1454: UserWarning: Dataframe headers not specified. Falling back to using column 0 as text and column 1 as labels.
  warnings.warn(


  0%|          | 0/12284 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/1536 [00:00<?, ?it/s]

Roberta
ACC:0.6645229566916314
F1:0.6597217953389898


In [ ]:
data = {'Aug': [ 'eda1', 'eda2', 'eda3', 'eda4','eda5'], # 'eda1', 'eda2', 'eda3', 'eda4','eda5'],
      #  'CNN_ACC': cnn_acc, 'CNN_F1':cnn_f1,
      #   'LSTM_ACC': lstm_acc, 'LSTM_F1':lstm_f1,
        'BERT_ACC': bert_acc, 'BERT_F1':bert_f1,
        'XLNET_ACC': xlnet_acc, 'XLNET_F1':xlnet_f1,
        'ROBERTA_ACC': roberta_acc, 'ROBERTA_F1':roberta_f1,}



base_resultados = pd.DataFrame.from_dict(data)

In [ ]:
base_resultados

Aug  BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
0  eda1  0.608515  0.590492   0.637496  0.630400     0.662651    0.647412
1  eda2  0.626425  0.605192   0.665825  0.653246     0.680967    0.675327
2  eda3  0.584175  0.565855   0.631960  0.613006     0.665174    0.657542
3  eda4  0.610062  0.585118   0.633181  0.625586     0.645392    0.625692
4  eda5  0.623901  0.603100   0.657685  0.647691     0.664523    0.659722

In [ ]:
base_resultados.describe()

BERT_ACC   BERT_F1  XLNET_ACC  XLNET_F1  ROBERTA_ACC  ROBERTA_F1
count  5.000000  5.000000   5.000000  5.000000     5.000000    5.000000
mean   0.610615  0.589951   0.645230  0.633986     0.663741    0.653139
std    0.016810  0.015886   0.015495  0.016449     0.012622    0.018311
min    0.584175  0.565855   0.631960  0.613006     0.645392    0.625692
25%    0.608515  0.585118   0.633181  0.625586     0.662651    0.647412
50%    0.610062  0.590492   0.637496  0.630400     0.664523    0.657542
75%    0.623901  0.603100   0.657685  0.647691     0.665174    0.659722
max    0.626425  0.605192   0.665825  0.653246     0.680967    0.675327